In [1]:
import spacy

In [2]:
model = spacy.load("../ru2/")

In [3]:
import pke

# initialize keyphrase extraction model, here TopicRank
extractor = pke.unsupervised.TopicRank()

# load the content of the document, here document is expected to be in raw
# format (i.e. a simple text file) and preprocessing is carried out using spacy
extractor.load_document(input='Ты жопа слона, а я бот-вертолёт.', spacy_model=model)

In [4]:
extractor.candidate_selection()

# candidate weighting, in the case of TopicRank: using a random walk algorithm
extractor.candidate_weighting()

# N-best selection, keyphrases contains the 10 highest scored candidates as
# (keyphrase, score) tuples
keyphrases = extractor.get_n_best(n=10)

In [5]:
keyphrases

[('вертолёт', 0.5), ('жопа слона', 0.5)]

In [9]:
pip install python-docx

Processing /home/memesrized/.cache/pip/wheels/97/4c/2e/68066cbf12b9b2e66403da8982aaf4f656d9f5cb5dc3179e82/python_docx-0.8.10-py3-none-any.whl
Note: you may need to restart the kernel to use updated packages.


In [14]:
"""Parser for html, docx, pdf."""

import re
from io import StringIO

from bs4 import BeautifulSoup
from docx import Document
from pdfminer3.converter import TextConverter
from pdfminer3.layout import LAParams
from pdfminer3.pdfinterp import PDFPageInterpreter, PDFResourceManager
from pdfminer3.pdfpage import PDFPage


class Parser:
    def __init__(self):
        self.mapper = {
            "html": self._html,
            "doc": self._docx,
            "docx": self._docx,
            "pdf": self._pdf,
        }

    def parse(self, path, ext="html"):
        return self.mapper[ext](path)

    def _docx(self, file_path: str) -> str:
        """Load a docx file and split document into pages.
        Args:
            file_path: path to docx file.
        Returns:
            list of pages.
        """
        doc = Document(file_path)
        full_text = []
        for para in doc.paragraphs:
            full_text.append(para.text)
        return "\n".join(full_text)

    def _html(self, path: str) -> str:
        """Split html content to pages.
        Args:
            raw_html: html content
        Returns:
            list of pages
        """
        with open(path) as file:
            raw_html = file.read()
        soup = BeautifulSoup(raw_html, features="lxml")

        # TODO: move to the config
        for div in soup.find_all(["header", "head", "nav", "footer"]):
            div.decompose()

        for div in soup.find_all(
            class_=["cookie-compliance__inner", "menu-selector", "page-search"]
        ):
            div.extract()

        for div in soup.find_all(id=["nav", "menuwrapper"]):
            div.extract()

        # replace non-breaking space
        return re.sub(r"\n+", "\n", soup.get_text())

    def _pdf(self, path: str) -> str:
        """Load a PDF file and split document to pages.
        Args:
            pdf: PDF file or path to file
        Returns:
            list of pages.
        """
        rsrcmgr = PDFResourceManager()
        retstr = StringIO()
        device = TextConverter(rsrcmgr, retstr, codec="utf-8", laparams=LAParams())
        list_of_pages = []
        with open(path, "rb") as pdf_file:
            interpreter = PDFPageInterpreter(rsrcmgr, device)
            password = ""
            maxpages = 0
            caching = True
            pagenos = set()

            for page in PDFPage.get_pages(
                pdf_file,
                pagenos,
                maxpages=maxpages,
                password=password,
                caching=caching,
                check_extractable=True,
            ):
                read_position = retstr.tell()
                interpreter.process_page(page)
                retstr.seek(read_position, 0)
                page_text = retstr.read()
                list_of_pages.append(page_text)
        device.close()
        retstr.close()
        return "\n".join(list_of_pages)

In [15]:
parser = Parser()

In [16]:
from pathlib import Path

In [20]:
docs = {}

for x in Path("../data/").rglob("*.*"):
    print(x)
    if x.suffix in [".docx", '.pdf']:
        docs[x] = parser.parse(x, ext=x.suffix[1:])

../data/prikl/000658_╨Т╨▓╨╡╨┤╨╡╨╜╨╕╨╡ ╨▓ MATLAB.docx
../data/prikl/000166_╨Ф╨╕╤Б╨║╤А╨╡╤В╨╜╨░╤П ╨╝╨░╤В╨╡╨╝╨░╤В╨╕╨║╨░.docx
../data/prikl/000122_╨У╨╡╨╛╨╝╨╡╤В╤А╨╕╤П.doc
../data/prikl/000657_╨Ю╤Б╨╜╨╛╨▓╤Л ╨┐╤А╨╛╨│╤А╨░╨╝╨╝╨╕╤А╨╛╨▓╨░╨╜╨╕╤П.docx
../data/prikl/000655_╨Р╨╗╨│╨╡╨▒╤А╨░.docx
../data/prikl/000124_╨Ь╨░╤В╨╡╨╝╨░╤В╨╕╤З╨╡╤Б╨║╨╕╨╣ ╨░╨╜╨░╨╗╨╕╨╖ I.doc
../data/progr/C1 - C2 - ╨Ю╤Б╨╜╨╛╨▓╤Л ╨┐╤А╨╛╨│╤А╨░╨╝╨╝╨╕╤А╨╛╨▓╨░╨╜╨╕╤П - 001857.pdf
../data/progr/C1 - C2 - ╨Ю╤Б╨╜╨╛╨▓╤Л ╨┤╨╕╤Б╨║╤А╨╡╤В╨╜╨╛╨╣ ╨╝╨░╤В╨╡╨╝╨░╤В╨╕╨║╨╕ - 000121.pdf
../data/progr/C2 - ╨Ь╨░╤В╨╡╨╝╨░╤В╨╕╤З╨╡╤Б╨║╨╕╨╣ ╨░╨╜╨░╨╗╨╕╨╖ II - 001859.pdf
../data/progr/C1 - ╨Р╤А╤Е╨╕╤В╨╡╨║╤В╤Г╤А╨░ ╨▓╤Л╤З╨╕╤Б╨╗╨╕╤В╨╡╨╗╤М╨╜╤Л╤Е ╤Б╨╕╤Б╤В╨╡╨╝ - 001860.pdf
../data/progr/C1 - ╨Ь╨░╤В╨╡╨╝╨░╤В╨╕╤З╨╡╤Б╨║╨╕╨╣ ╨░╨╜╨░╨╗╨╕╨╖ I - 001856.pdf
../data/progr/C1 - C2 - ╨Р╨╗╨│╨╡╨▒╤А╨░ ╨╕ ╨│╨╡╨╛╨╝╨╡╤В╤А╨╕╤П - 000160.pdf
../data/mat/040542 Java-╤В╨╡╤Е╨╜╨╛╨╗╨╛╨│╨╕╨╕. ╨з╨░╤Б╤В╤М 2.docx
../data/mat/040544_╨б╨╡╤В╨╕ ╨Я╨╡╤В╤А╨╕ ╨╕ ╨┐╤А╨╡╨┤╤Б╤В╨░╨▓╨╗╨╡╨╜╨╕╨╡ ╨┐╤А╨╛╤Ж╨╡╤Б╤Б╨╛╨▓.do

../data/mat/040921_╨Ъ╤Г╤А╤Б╨╛╨▓╨░╤П ╤А╨░╨▒╨╛╤В╨░ 3.docx
../data/mat/002316_╨д╤Г╨╜╨║╤Ж╨╕╨╛╨╜╨░╨╗╤М╨╜╤Л╨╣ ╨░╨╜╨░╨╗╨╕╨╖ 2019.docx
../data/mat/002231_╨Т╨▓╨╡╨┤╨╡╨╜╨╕╨╡ ╨▓ ╤Б╨┐╨╡╤Ж╨╕╨░╨╗╤М╨╜╨╛╤Б╤В╤М.docx


In [22]:
i=0
for x in docs:
    i+=1
    print(x)
    print("\n")
    print(docs[x])
    print("-"*100)
    if i>10:
        break

../data/prikl/000658_╨Т╨▓╨╡╨┤╨╡╨╜╨╕╨╡ ╨▓ MATLAB.docx


Санкт-Петербургский государственный университет







Р А Б О Ч А Я  П Р О Г Р А М М А
учебной дисциплины 
Введение в MATLAB
Introduction to MATLAB


Язык(и) обучения
_________русский___________


Трудоёмкость (границы трудоёмкости) в зачетных единицах: 4
 
Регистрационный номер рабочей программы: 000658













Санкт-Петербург
2020

Раздел 1.	Характеристики учебных занятий
1.1.	Цели и задачи учебных занятий
Целью учебных занятий является ознакомление обучающихся с возможностями интерактивной среды MATLAB и основами программирования на языке MATLAB, формирование навыков решения средствами среды MATLAB различных практических задач, возникающих при изучении других естественнонаучных дисциплин.
Основными задачами дисциплины являются:
изучение системы MATLAB как высокоэффективного инструмента для решения различных математических задач, визуализации результатов вычислений, создания наукоемкого программного обеспечения;
формировани

In [23]:
from tqdm import tqdm

In [27]:
keywords = {}

for x in tqdm(docs):
    extractor = pke.unsupervised.SingleRank()
    extractor.load_document(input=docs[x], spacy_model=model)
    extractor.candidate_selection()
    extractor.candidate_weighting()
    keyphrases = extractor.get_n_best(n=30)
    keywords[x] = keyphrases

100%|██████████| 109/109 [01:05<00:00,  1.67it/s]


In [28]:
keywords

{PosixPath('../data/prikl/000658_╨Т╨▓╨╡╨┤╨╡╨╜╨╕╨╡ ╨▓ MATLAB.docx'): [('формирование навыков решения средствами среды matlab различных практических задач',
   0.039100061599006586),
  ('основные типы данных matlab', 0.03232280828561974),
  ('основные компоненты системы matlab', 0.03179444535255291),
  ('выходных аргументов функций matlab', 0.03153891278825851),
  ('основные конструкции языка matlab', 0.03063517016940676),
  ('формирование навыков использования пакета matlab', 0.030457847952816697),
  ('основные элементы языка matlab', 0.030169562758420882),
  ('формировании навыков применения пакета matlab', 0.029104706110244145),
  ('изучение системы matlab', 0.02867890919400167),
  ('навыками использования пакета matlab', 0.027979910225851928),
  ('вычислительные алгоритмы средствами пакета matlab', 0.027519426144755884),
  ('операторы языка matlab', 0.027384801231206842),
  ('развития системы matlab', 0.027301722498965786),
  ('системе matlab', 0.027287963121342865),
  ('справочная д

In [32]:
import json

with open("../data/standards_text.json") as file:
    prof = json.load(file)

In [37]:
prof = {x['standard_name']:x['text'] for x in prof}

In [40]:
prof_keywords = {}

for x in tqdm(prof):
    extractor = pke.unsupervised.SingleRank()
    extractor.load_document(input=prof[x], spacy_model=model)
    extractor.candidate_selection()
    extractor.candidate_weighting()
    keyphrases = extractor.get_n_best(n=30)
    prof_keywords[x] = keyphrases

100%|██████████| 1336/1336 [25:43<00:00,  1.16s/it]


In [42]:
with open("../data/prof_keywords.json", 'w') as file:
    json.dump(prof_keywords, file, indent=4, ensure_ascii=False)

In [46]:
keywords = {x.stem: keywords[x] for x in keywords}

In [47]:
with open("../data/keywords.json", 'w') as file:
    json.dump(keywords, file, indent=4, ensure_ascii=False)

In [43]:
keywords

{PosixPath('../data/prikl/000658_╨Т╨▓╨╡╨┤╨╡╨╜╨╕╨╡ ╨▓ MATLAB.docx'): [('формирование навыков решения средствами среды matlab различных практических задач',
   0.039100061599006586),
  ('основные типы данных matlab', 0.03232280828561974),
  ('основные компоненты системы matlab', 0.03179444535255291),
  ('выходных аргументов функций matlab', 0.03153891278825851),
  ('основные конструкции языка matlab', 0.03063517016940676),
  ('формирование навыков использования пакета matlab', 0.030457847952816697),
  ('основные элементы языка matlab', 0.030169562758420882),
  ('формировании навыков применения пакета matlab', 0.029104706110244145),
  ('изучение системы matlab', 0.02867890919400167),
  ('навыками использования пакета matlab', 0.027979910225851928),
  ('вычислительные алгоритмы средствами пакета matlab', 0.027519426144755884),
  ('операторы языка matlab', 0.027384801231206842),
  ('развития системы matlab', 0.027301722498965786),
  ('системе matlab', 0.027287963121342865),
  ('справочная д

In [41]:
prof_keywords

{'Мостовщик': [('способы контроля качества выполненных работ',
   0.06175698363682297),
  ('осуществлении сложных дорожных работ различных видов',
   0.061158671900728934),
  ('осуществлении сложных дорожных работ', 0.05783153404235261),
  ('средней сложности дорожных работ', 0.05383004244705451),
  ('выполнении сложных дорожных работ', 0.05343870363581149),
  ('соответствие качества выполненных работ установленным/',
   0.05341977956028688),
  ('контроль качества выполненных работ', 0.05217833870091352),
  ('оценку качества выполненных работ', 0.051230533012308246),
  ('способы выполнения работ', 0.051042505604644746),
  ('способы производства разбивочных работ', 0.04892886372351649),
  ('правила применения средств индивидуальной защиты', 0.04816177713456498),
  ('выполнении дорожных работ', 0.047438866575503336),
  ('выполнению дорожных работ', 0.047280568236181555),
  ('качеству выполнения работ', 0.044060202170962355),
  ('правила применения ручного инструмента', 0.0420466597934701

In [38]:
prof["Мостовщик"]

'Выполнение подготовительно-заключительных операций при подготовке участка к укладке покрытия.\nРазборка выстилок и мостовых.\nВыполнение работ по подсыпке грунта у придорожных столбов с трамбованием.\nПоддерживать состояние рабочего места в соответствии с требованиями охраны труда, противопожарной, промышленной и экологической безопасности.\nПодготавливать инструмент и средства малой механизации к работе.\nОчищать участок перед укладкой покрытия.\nШтабелировать камень или иные используемые материалы.\nОчищать и сортировать щебень, гравий и песок.\nПроизводить разборку каменных мостовых и каменных выстилок.\nИспользовать ручной инструмент и средства малой механизации при осуществлении трудовых функций.\nВыполнять задания в соответствии с технологическим процессом производства работ.\nВыполнять моечно-очистные операции по окончании работ.\nВыполнять правила охраны труда, противопожарной и экологической безопасности при ведении работ.\nИспользовать средства индивидуальной защиты.\nОказыв